In [ ]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [ ]:
import torch
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
import nltk
import numpy as np
from sklearn.metrics import accuracy_score

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
import warnings
warnings.filterwarnings("ignore")
nltk.download('averaged_perceptron_tagger')

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

cuda


In [ ]:
'/content/drive/MyDrive/667/transition/data/dev.txt'

'/content/drive/MyDrive/667/transition/data/dev.txt'

In [ ]:
vocab_file = open('/content/drive/MyDrive/667/transition/data/vocab.txt')
vocab_data = vocab_file.read()

In [ ]:
vocab_data

"<unk>\t1\n.\t9731\n,\t9303\nthe\t8173\nto\t4525\nof\t4521\na\t3881\nand\t3041\nin\t3016\n's\t1905\nThe\t1732\nis\t1620\nfor\t1617\nthat\t1541\n$\t1500\n``\t1443\n''\t1396\n##\t1375\nsaid\t1229\non\t1073\n%\t1014\nit\t1010\nMr.\t1002\nby\t947\nfrom\t933\nas\t930\nmillion\t918\nat\t906\nwas\t878\nare\t877\nbe\t827\nwith\t808\nits\t759\nwill\t755\nn't\t735\nhas\t698\nhave\t689\nan\t652\nhe\t601\n####\t575\n###\t540\n#\t512\ncompany\t507\nBut\t437\n#.#\t429\nyear\t429\nwere\t427\nor\t423\n#.##\t422\nwould\t418\nsays\t418\nthey\t412\nthis\t404\nwhich\t402\nabout\t396\nmore\t393\nIn\t389\nmarket\t384\nhad\t373\nbillion\t364\nup\t351\nalso\t347\nhis\t346\ntheir\t327\nbeen\t323\nthan\t320\n:\t318\nnot\t306\nnew\t305\nbut\t296\nU.S.\t295\nIt\t294\n--\t293\none\t282\nshare\t273\nshares\t272\n##.#\t268\nI\t266\nother\t261\nwho\t257\nyears\t251\nNew\t246\nsome\t245\nstock\t244\nCorp.\t230\ntrading\t228\ncould\t227\nlast\t226\nout\t220\nall\t217\nHe\t211\ndo\t209\ncan\t208\nsales\t204\nonly\t200\n

In [ ]:
## Create the word-to-Id,POS tag-to-Id,Three transition-to-Id dictionary
word_to_id = {}
id_to_word = {}
tag_to_id = {}
id_to_tag = {}
transition_to_id = {'SHIFT': 0, 'REDUCE_L': 1, 'REDUCE_R': 2}
id_to_transition = {value: key for key, value in transition_to_id.items()}

In [ ]:
for i, line in enumerate(vocab_data.split('\n')):
  word, freq = line.split()
  word_to_id[word] = i
  id_to_word[i] = word

In [ ]:
n_vocab = len(word_to_id)
n_vocab

9151

In [ ]:
file = open('/content/drive/MyDrive/667/transition/data/train.txt')
whole_data = file.read()

In [ ]:
whole_data

"Bell , based in Los Angeles , makes and distributes electronic , computer and building products . ||| SHIFT SHIFT REDUCE_R SHIFT SHIFT SHIFT SHIFT REDUCE_L REDUCE_R REDUCE_R REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_L SHIFT REDUCE_R SHIFT REDUCE_R SHIFT SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_L REDUCE_R SHIFT REDUCE_R\n`` Apparently the commission did not really believe in this ideal . '' ||| SHIFT SHIFT SHIFT SHIFT REDUCE_L SHIFT SHIFT SHIFT SHIFT REDUCE_L REDUCE_L REDUCE_L REDUCE_L REDUCE_L REDUCE_L SHIFT SHIFT SHIFT REDUCE_L REDUCE_R REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R\nBut about ## % of the insiders , according to SEC figures , file their reports late . ||| SHIFT SHIFT SHIFT REDUCE_L SHIFT REDUCE_L SHIFT SHIFT SHIFT REDUCE_L REDUCE_R REDUCE_R SHIFT SHIFT SHIFT SHIFT SHIFT REDUCE_L REDUCE_R REDUCE_R SHIFT SHIFT REDUCE_L REDUCE_L REDUCE_L REDUCE_L REDUCE_L SHIFT SHIFT REDUCE_L REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R\nNot all those who wrote oppose the c

In [ ]:
tag_idx = 0
for line in whole_data.split('\n'):
  text, transition = line.split('|||')
  tag = [tuple[1] for tuple in nltk.pos_tag(text.split())]

  for pos in tag:
    if pos not in tag_to_id.keys():
      tag_to_id[pos] = tag_idx
      id_to_tag[tag_idx] = pos
      tag_idx += 1

In [ ]:
lines = whole_data.split('\n')
lines[0]

'Bell , based in Los Angeles , makes and distributes electronic , computer and building products . ||| SHIFT SHIFT REDUCE_R SHIFT SHIFT SHIFT SHIFT REDUCE_L REDUCE_R REDUCE_R REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_L SHIFT REDUCE_R SHIFT REDUCE_R SHIFT SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_R SHIFT REDUCE_L REDUCE_R SHIFT REDUCE_R'

In [ ]:
id_to_tag
id_to_transition

{0: 'NNP',
 1: ',',
 2: 'VBN',
 3: 'IN',
 4: 'VBZ',
 5: 'CC',
 6: 'JJ',
 7: 'NN',
 8: 'NNS',
 9: '.',
 10: '``',
 11: 'RB',
 12: 'DT',
 13: 'VBD',
 14: 'VB',
 15: "''",
 16: 'VBG',
 17: 'TO',
 18: 'VBP',
 19: 'PRP$',
 20: 'PDT',
 21: 'WP',
 22: 'MD',
 23: 'JJR',
 24: 'PRP',
 25: 'WRB',
 26: 'RBR',
 27: ':',
 28: 'POS',
 29: 'FW',
 30: 'CD',
 31: 'WDT',
 32: 'NNPS',
 33: 'RP',
 34: 'EX',
 35: 'JJS',
 36: '$',
 37: '#',
 38: 'RBS',
 39: 'UH',
 40: 'WP$',
 41: 'SYM',
 42: 'LS'}

{0: 'SHIFT', 1: 'REDUCE_L', 2: 'REDUCE_R'}

## Dataset Class

In [ ]:
class ParserDataset(Dataset):
  def __init__(self, filename, n_samples=1000,train=True):
    file = open('/content/drive/MyDrive/667/transition/data/{}.txt'.format(filename))
    whole_data = file.read()
    self.texts = []
    self.tags = []
    self.transitions = []
    lines = whole_data.split('\n')
    if train:
      lines = lines[:n_samples]
    else:
      lines = lines[-n_samples:]
    for line in lines:
      text, transition = line.split('|||')
      tag = [tag_to_id[tuple[1]] for tuple in nltk.pos_tag(text.split())]
      text = [word_to_id[word] if word in word_to_id.keys() else 0 for word in text.split()]
      transition = [transition_to_id[trans] for trans in transition.split()]
      self.texts.append(text)
      self.tags.append(tag)
      self.transitions.append(transition)
  
  def __len__(self):
    return len(self.texts)
  
  def __getitem__(self,idx):
    text = self.texts[idx]
    tag = self.tags[idx]
    transition = self.transitions[idx]
    ##return the dictionary with the [text Id & PoS tag] along with it.
    data = [(text[i], tag[i]) for i in range(len(text))]
    return {'data': data, 'transition': transition}

In [ ]:
dataset = ParserDataset('train')

In [ ]:
len(dataset)

1000

In [ ]:
dataloader = DataLoader(dataset, batch_size=16, shuffle=False,collate_fn=lambda x: x )
for i_batch, sample_batched in enumerate(dataloader):
  print(len(sample_batched))
  data, transitions = sample_batched[0].values()
  #transitions = sample_batched[0]['transition']
  print(len(data),transitions,len(transitions))
  print(data,i_batch)
  break

16
17 [0, 0, 2, 0, 0, 0, 0, 1, 2, 2, 2, 0, 2, 0, 1, 0, 2, 0, 2, 0, 0, 2, 0, 2, 0, 2, 0, 2, 0, 1, 2, 0, 2] 33
[(2106, 0), (2, 1), (353, 2), (8, 3), (890, 0), (924, 0), (2, 1), (511, 4), (7, 5), (8429, 4), (1286, 6), (2, 1), (274, 7), (7, 5), (465, 7), (199, 8), (1, 9)] 0


In [ ]:
torch.tensor(transitions, dtype=torch.long, device=device).view(-1, 1)

In [ ]:
def train_operation(buffer,stack,arcs,transitions,idx):
  ##apply the gold standard
  if transitions[idx].item() == transition_to_id['SHIFT'] and len(buffer) > 0:
    stack.append(buffer[0])
    buffer = buffer[1:]
  elif transitions[idx].item() == transition_to_id['REDUCE_L'] and len(stack) >= 3:
    if stack[-1] in arcs['left-arc']:
      left_arcs = arcs['left-arc'][stack[-1]]
    else:
      left_arcs = {}
    left_arcs[len(left_arcs)] = stack[-2]
    arcs['left-arc'][stack[-1]] = left_arcs
    stack.remove(stack[-2])
  elif transitions[idx].item() == transition_to_id['REDUCE_R'] and len(stack) >= 3:
    if stack[-2] in arcs['right-arc'].keys():
      right_arcs = arcs['right-arc'][stack[-2]]
    else:
      right_arcs = {}
    right_arcs[len(right_arcs)] = stack[-1]
    arcs['right-arc'][stack[-2]] = right_arcs
    stack.remove(stack[-1])

def eval_operation(buffer,stack,arcs,topi):
  if topi.item() == transition_to_id['SHIFT'] and len(buffer) > 0:
    stack.append(buffer[0])
    buffer = buffer[1:]
  elif topi.item() == transition_to_id['REDUCE_L'] and len(stack) >= 3:
    if stack[-1] in arcs['left-arc']:
      left_arcs = arcs['left-arc'][stack[-1]]
    else:
      left_arcs = {}
    left_arcs[len(left_arcs)] = stack[-2]
    arcs['left-arc'][stack[-1]] = left_arcs
    stack.remove(stack[-2])
  elif topi.item() == transition_to_id['REDUCE_R'] and len(stack) >= 3:
    if stack[-2] in arcs['right-arc'].keys():
      right_arcs = arcs['right-arc'][stack[-2]]
    else:
      right_arcs = {}
      right_arcs[len(right_arcs)] = stack[-1]
      arcs['right-arc'][stack[-2]] = right_arcs
      stack.remove(stack[-1])

In [ ]:
def input_and_output(model, sample_batched, criterion, train=True):
  stack = ['ROOT']
  arcs = {'left-arc': {}, 'right-arc': {}}
  ##if batch size is 1. otherwise have to loop over.
  data, transitions = sample_batched[0].values()
  transitions = torch.tensor(transitions, dtype=torch.long, device=device).view(-1, 1)
  buffer = [tuple(item) for item in data]
  loss = 0
  operations = []
  for idx in range(len(transitions)):
    if len(buffer) != 0 or (len(stack) != 1 and stack[0] == 'ROOT'):
      words = [-1] * 6
      tags = [-1] * 6
      ##currently only taking the top of Buffer and stack features not Arc's created features.
      for i in range(3):
        if len(buffer) > i:
          words[i] = buffer[i][0]
          tags[i] = buffer[i][1]
      for i in range(3):
        if len(stack) > i + 1:
          words[i + 3] = stack[i + 1][0]
          tags[i + 3] = stack[i + 1][1]
      
      words = torch.tensor(words, dtype=torch.long, device=device)
      tags = torch.tensor(tags, dtype=torch.long, device=device)
      output = model(words, tags)
      loss += criterion(output, transitions[idx])
      topv, topi = output.topk(1)
      operations.append(id_to_transition[topi.item()])

      if train:
        ##apply the gold standard
        train_operation(buffer,stack,arcs,transitions,idx)
        
      else:
        ##For Inference Apply the previous predicted label
        eval_operation(buffer,stack,arcs,topi)
      #print(arcs)
  return transitions, operations, loss

In [ ]:
class ParsingNet(nn.Module):
    def __init__(self, n_vocab, embedding_size=100, hidden_size=500):
        super(ParsingNet, self).__init__()
        self.embedding_size = embedding_size
        self.hidden_size = hidden_size
        self.n_vocab = n_vocab
        self.word_embed = nn.Embedding(self.n_vocab, self.embedding_size)
        self.tag_embed = nn.Embedding(len(tag_to_id), self.embedding_size)
        self.linear = nn.Linear(self.embedding_size * 6 * 2, self.hidden_size)
        self.output = nn.Linear(self.hidden_size, len(transition_to_id))


    def forward(self, words, tags):
        word_embeds =[]
        tag_embeds = []
        ## Currently Random & zero embedding used,need to change this to pre trained word embedding
        for i in range(len(words)):
            word = words[i]
            tag = tags[i]
            if word != -1:
                word_embed = self.word_embed(word).unsqueeze(0).view(1, -1)
                tag_embed = self.tag_embed(tag).unsqueeze(0).view(1, -1)
            else:
                word_embed = torch.tensor([0]*self.embedding_size, dtype=torch.float, device=device).view(1, -1)
                tag_embed = torch.tensor([0] * self.embedding_size, dtype=torch.float, device=device).view(1, -1)
            word_embeds.append(word_embed.squeeze(0))
            tag_embeds.append(tag_embed.squeeze(0))

        word_embeds = torch.cat(word_embeds)
        tag_embeds = torch.cat(tag_embeds)
        input = torch.cat((word_embeds, tag_embeds), -1).unsqueeze(0)
        output = F.relu(self.linear(input))
        output = F.log_softmax(self.output(output), dim=1)
        return output

In [ ]:
model = ParsingNet(n_vocab).to(device)

In [ ]:
model

ParsingNet(
  (word_embed): Embedding(9151, 100)
  (tag_embed): Embedding(43, 100)
  (linear): Linear(in_features=1200, out_features=500, bias=True)
  (output): Linear(in_features=500, out_features=3, bias=True)
)

In [ ]:
learning_rate=0.0003
weight_decay=1e-10
n_epochs=10
filename='train'

In [ ]:
dataset = ParserDataset(filename,n_samples=1000)
criterion = nn.NLLLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate, weight_decay=weight_decay)

In [ ]:
def train(dataset, model, criterion, optimizer):
    dataloader = DataLoader(dataset, batch_size=1, shuffle=False,collate_fn=lambda x: x)
    losses = []
    all_truths = []
    all_operations = []
    for i_batch, sample_batched in enumerate(dataloader):
        #print(i_batch)
        optimizer.zero_grad()
        transitions, operations, loss = input_and_output(model, sample_batched, criterion)
        losses.append(loss.item() / len(operations))
        loss.backward()
        optimizer.step()
    all_truths.append([id_to_transition[i[0].item()] for i in transitions])
    all_operations.append(operations)
    accuracy = accuracy_score(np.array(all_truths).reshape(-1), np.array(all_operations).reshape(-1))
    return losses, accuracy

In [ ]:
losses  = []
acc = []
for i in range(n_epochs):
    total_loss, accuracy = train(dataset, model, criterion, optimizer)
    print('Iter: {}, Total loss: {}, Accuracy: {}'.format(i, np.mean(total_loss), accuracy))
    losses.append(np.mean(total_loss))
    acc.append(accuracy)

In [ ]:
def evaluate(model):
    dataset_eva = ParserDataset(filename='dev', n_samples=1000,train=False)
    criterion = nn.NLLLoss()
    dataloader_eva = DataLoader(dataset_eva, batch_size=1, shuffle=False,collate_fn=lambda x: x)
    losses = []
    all_truths = []
    all_operations = []
    for i_batch, sample_batched in enumerate(dataloader_eva):
        transitions, operations, loss = input_and_output(model, sample_batched, criterion,False)
        losses.append(loss.item() / len(operations))
        all_truths.append([id_to_transition[i[0].item()] for i in transitions])
        all_operations.append(operations)
    #accuracy = accuracy_score(np.array(all_truths).reshape(-1), np.array(all_operations).reshape(-1))
    #print('Loss: {}, Accurarcy: {}'.format(np.mean(losses), accuracy))
    print('Predicted: ', all_operations)
    print('Ground Truth: ', all_truths)
    return all_operations,all_truths

In [ ]:
all_operations,all_truths=evaluate(model)

Predicted:  [['SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT'], ['SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT'], ['SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', 'SHIFT', '

In [ ]:
all_truths_fl = [item for sublist in all_truths for item in sublist]
all_operations_fl = [item for sublist in all_operations for item in sublist]

In [ ]:
accuracy_score(all_truths_fl,all_operations_fl)
set(all_operations_fl)

0.449618320610687

{'REDUCE_L', 'REDUCE_R', 'SHIFT'}

In [ ]:
#0.4496 True
#
from sklearn.metrics import classification_report
target_names = ['REDUCE_L', 'REDUCE_R', 'SHIFT']
print(classification_report(all_truths_fl, all_operations_fl, target_names=target_names))

              precision    recall  f1-score   support

    REDUCE_L       0.26      0.05      0.08      3967
    REDUCE_R       0.27      0.28      0.28      3693
       SHIFT       0.52      0.72      0.61      8060

    accuracy                           0.45     15720
   macro avg       0.35      0.35      0.32     15720
weighted avg       0.40      0.45      0.40     15720



In [ ]:
len(all_truths_fl)
len(all_operations_fl)

15720

15720

## Reference:
- https://github.com/yc930401/Transition_based_dependency_parsing-pytorch/blob/master/dependency_parsing.py